In [1]:
import numpy as np
import pandas as pd

import os
import urllib.request
import sys

from sklearn.model_selection import train_test_split

In [2]:
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
import torch.nn.functional as f
import torch.optim as optim

import torchvision
from torchvision.transforms import v2
from torchvision import models
from torchvision.models import resnet50, ResNet50_Weights
import torch.optim.lr_scheduler as lr_scheduler

import random
from PIL import Image
import matplotlib.pyplot as plt

In [3]:
df = pd.read_csv('/kaggle/input/fakenews-fakedit/Dataset/df_balanced_resized.csv')

In [4]:
df.head(10)

author                                        clean_title  \
0   BruxellesBlonde                                  sooooo satisfying   
1            korkow   the chips fell out of this chocolate chip cookie   
2    kyletheheroman              has anyone seen a square cloud before   
3        FledPotato                      it almost seems to smile back   
4   allhundredyears                  this tape deck has seen some shit   
5         spyder_19   saw an interesting sign at the store so i got it   
6        Not3Shabby                          inherent paradox scrabeck   
7          mikewall  gop senate candidate kelli ward complained mcc...   
8      worldnews_SS  christians fleeing iraqs mosul region to provi...   
9  todayilearned_SS  til pegi europes video game in only to turn to...   

    created_utc        domain  hasImage      id  \
0  1.537968e+09     i.redd.it      True  9j2gd1   
1  1.384738e+09   i.imgur.com      True  1qv2m9   
2  1.551516e+09     i.redd.it      True  awfsgw   
3  1.522871e+09     i.redd.it      True  89ssvs   
4  1.426363e+09     imgur.com      True  2z1tha   
5  1.564682e+09     i.redd.it      True  ckrv3k   
6  1.489213e+09     imgur.com      True  5yrdcs   
7  1.535296e+09  newsweek.com      True  9ag51l   
8  1.458731e+09  engadget.com      True  4bm0cs   
9  1.486354e+09   nytimes.com      True  5sc05y   

                                           image_url linked_submission_id  \
0  https://preview.redd.it/bjlftqsj3lo11.jpg?widt...                  NaN   
1  https://external-preview.redd.it/ESPM-tTuK3wer...                  NaN   
2  https://preview.redd.it/trqkt1rx4oj21.jpg?widt...                  NaN   
3  https://preview.redd.it/yf1j0rvq4yp01.jpg?widt...                  NaN   
4  https://external-preview.redd.it/QFHuRDeu_v1cm...                  NaN   
5  https://preview.redd.it/ketwpycjmvd31.jpg?widt...                  NaN   
6  https://external-preview.redd.it/g3nNRMvtW8FCT...                  NaN   
7  https://external-preview.redd.it/3c79PddPA_og2...                  NaN   
8  https://external-preview.redd.it/xNKcWQsoGpWr3...                  NaN   
9  https://external-preview.redd.it/PL4PyhChdGdhF...                  NaN   

   num_comments  score             subreddit  upvote_ratio  6_way_label  \
0           3.0     15     mildlyinteresting          0.75            0   
1           4.0      8  misleadingthumbnails          0.59            2   
2           6.0      4     mildlyinteresting          0.60            0   
3           9.0    212            pareidolia          0.98            2   
4           2.0      6            pareidolia          0.88            2   
5           2.0     32     mildlyinteresting          0.87            0   
6           0.0      4       fakealbumcovers          0.83            1   
7          15.0    243           nottheonion          0.95            0   
8          20.0     10    subredditsimulator          0.92            3   
9          61.0      5    subredditsimulator          0.86            3   

   binary_label  
0             0  
1             1  
2             0  
3             1  
4             1  
5             0  
6             1  
7             0  
8             1  
9             1

In [5]:
%%capture

! pip install bert-serving-server
! pip install bert-serving-client
! pip install torch transformers

In [6]:
import torch
from transformers import BertModel, BertTokenizer

# Load pre-trained BERT model and tokenizer
model_name = 'bert-base-uncased'
tokenizer = BertTokenizer.from_pretrained(model_name)
bert_model = BertModel.from_pretrained(model_name, output_hidden_states = True)

# Put the model in evaluation mode, which turns off dropout regularization which is used in training.
bert_model.eval()

tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

BertModel(
  (embeddings): BertEmbeddings(
    (word_embeddings): Embedding(30522, 768, padding_idx=0)
    (position_embeddings): Embedding(512, 768)
    (token_type_embeddings): Embedding(2, 768)
    (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (encoder): BertEncoder(
    (layer): ModuleList(
      (0-11): 12 x BertLayer(
        (attention): BertAttention(
          (self): BertSdpaSelfAttention(
            (query): Linear(in_features=768, out_features=768, bias=True)
            (key): Linear(in_features=768, out_features=768, bias=True)
            (value): Linear(in_features=768, out_features=768, bias=True)
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (output): BertSelfOutput(
            (dense): Linear(in_features=768, out_features=768, bias=True)
            (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
            (dropout): Dropout(p=0.1, inplace=False

In [7]:
def get_bert_embedding(text):
    # Tokenize input text and get token IDs and attention mask
    inputs = tokenizer.encode_plus(text, add_special_tokens = True, return_tensors='pt', max_length=80, truncation=True, padding='max_length')

    return inputs['input_ids'].squeeze(0), inputs['attention_mask'].squeeze(0)

In [8]:
from sklearn.model_selection import train_test_split
df_train, df_test = train_test_split(df, test_size=0.2, stratify=df["binary_label"])
df_test, df_val = train_test_split(df_test, test_size=0.5, stratify=df_test["binary_label"])

In [9]:
class FakedditDataset(Dataset):
    def __init__(self, df, text_field="clean_title", label_field="binary_label", image_id="id"):
        self.df = df.reset_index(drop=True)
        self.text_field = text_field
        self.label_field = label_field
        self.image_id = image_id

        self.img_size = 256
        # Using the pre-calculated ImageNet mean and std values for normalization
        self.mean, self.std = [0.485, 0.456, 0.406], [0.229, 0.224, 0.225]

        self.transform_func = v2.Compose(
                [   v2.Resize(256),
                    v2.ToImage(),
                    v2.ToDtype(torch.float32, scale=True),
                    v2.Normalize(self.mean, self.std)
                    ])

    def __getitem__(self, index):
        text = str(self.df.at[index, self.text_field])
        label = self.df.at[index, self.label_field]
        img_path = "/kaggle/input/fakenews-fakedit/Dataset/images/" + self.df.at[index, self.image_id] + ".jpg"

        image = Image.open(img_path)
        img = self.transform_func(image)

        input_ids, attention_mask = get_bert_embedding(text)

        return input_ids, attention_mask, label, img

    def __len__(self):
        return self.df.shape[0]

In [10]:
train_dataset = FakedditDataset(df_train)
test_dataset = FakedditDataset(df_test)
val_dataset = FakedditDataset(df_val)

In [11]:
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=32, shuffle=True)

print(len(train_loader))

# Verifying dataset was created accurately
input_ids, attention_mask, label, img = next(iter(train_loader))
print(input_ids.shape, attention_mask.shape, label.shape, img.shape)

1643
torch.Size([32, 80]) torch.Size([32, 80]) torch.Size([32]) torch.Size([32, 3, 256, 256])


In [12]:
class EarlyStopping:
    def __init__(self, patience=4, verbose=False, delta=0):
        self.patience = patience
        self.verbose = verbose
        self.counter = 0
        self.best_loss = None
        self.early_stop = False
        self.delta = delta

    def __call__(self, val_loss):
        if self.best_loss is None:
            self.best_loss = val_loss
        elif val_loss > self.best_loss + self.delta:
            self.counter += 1
            if self.verbose:
                print(f"EarlyStopping counter: {self.counter} out of {self.patience}")
            if self.counter >= self.patience:
                self.early_stop = True
        else:
            self.best_loss = val_loss
            self.counter = 0

In [13]:
labels = df_train["binary_label"].values  

print(labels)
print("Unique labels:", np.unique(labels))
# assert set(np.unique(labels)).issubset({0, 1}), "🔥 Labels must be 0 or 1 for binary classification!"

[0 0 0 ... 0 1 1]
Unique labels: [0 1]


In [14]:
class SelfAttentionFusion(nn.Module):
    def __init__(self, embed_dim):
        super().__init__()
        self.attn = nn.Linear(embed_dim * 2, 2)
        self.softmax = nn.Softmax(dim=1)

    def forward(self, x_text, x_img):
        stacked = torch.stack([x_text, x_img], dim=1)  # (B, 2, D)
        attn_weights = self.softmax(self.attn(torch.cat([x_text, x_img], dim=1))).unsqueeze(2)  # (B, 2, 1)
        fused = (attn_weights * stacked).sum(dim=1)  # (B, D)
        return fused

In [15]:
class BERTResNetClassifier(nn.Module):
    def __init__(self, num_classes=2):
        super(BERTResNetClassifier, self).__init__()

        self.num_classes = num_classes

        # Image model
        self.image_model = resnet50(weights=ResNet50_Weights.IMAGENET1K_V1)
        self.fc_image = nn.Linear(1000, 512)
        self.drop_img = nn.Dropout(p=0.3)

        # Text model
        self.text_model = BertModel.from_pretrained("bert-base-uncased")
        self.fc_text = nn.Linear(self.text_model.config.hidden_size, 512)
        self.drop_text = nn.Dropout(p=0.3)

        # Attention-based fusion
        self.fusion = SelfAttentionFusion(embed_dim=512)

        # Final classification
        self.fc_final = nn.Linear(512, num_classes)

    def forward(self, image, text_input_ids, text_attention_mask):
        # Image path
        x_img = self.image_model(image)
        x_img = self.drop_img(x_img)
        x_img = self.fc_image(x_img)

        # Text path
        x_text_last_hidden = self.text_model(
            input_ids=text_input_ids,
            attention_mask=text_attention_mask,
            return_dict=False
        )[0][:, 0, :]
        x_text = self.drop_text(x_text_last_hidden)
        x_text = self.fc_text(x_text)

        # Fusion
        x_fused = self.fusion(x_text, x_img)

        # Final classifier
        logits = self.fc_final(x_fused)
        return logits


In [16]:
from sklearn.utils import compute_class_weight
# import torch_xla.core.xla_model as xm

In [17]:
device = "cuda" if torch.cuda.is_available() else "cpu"
print(device)
model = BERTResNetClassifier(num_classes=2)

if torch.cuda.device_count() > 1:
    print(f"Using {torch.cuda.device_count()} GPUs!")
    model = nn.DataParallel(model)
model = model.to(device)

cuda


Downloading: "https://download.pytorch.org/models/resnet50-0676ba61.pth" to /root/.cache/torch/hub/checkpoints/resnet50-0676ba61.pth
100%|██████████| 97.8M/97.8M [00:00<00:00, 172MB/s]


Using 2 GPUs!


In [18]:
import torch.nn.functional as F

class FocalLoss(nn.Module):
    def __init__(self, alpha=None, gamma=2.0, reduction='mean'):
        super(FocalLoss, self).__init__()
        self.alpha = alpha
        self.gamma = gamma
        self.reduction = reduction

    def forward(self, inputs, targets):
        ce_loss = F.cross_entropy(inputs, targets, weight=self.alpha, reduction='none')
        pt = torch.exp(-ce_loss)  # Prob of correct class
        focal_loss = ((1 - pt) ** self.gamma) * ce_loss

        if self.reduction == 'mean':
            return focal_loss.mean()
        elif self.reduction == 'sum':
            return focal_loss.sum()
        else:
            return focal_loss

In [19]:
from sklearn.utils.class_weight import compute_class_weight

class_weights = compute_class_weight(class_weight='balanced', classes=np.unique(labels), y=labels)
class_weights = torch.tensor(class_weights, dtype=torch.float).to(device)

criterion = FocalLoss(alpha=class_weights, gamma=2.0)
# criterion = nn.CrossEntropyLoss(weight=class_weights)
# optimizer = torch.optim.Adam(model.parameters(), lr=1e-5, weight_decay=1e-4)
optimizer = torch.optim.Adam([
    {'params': model.module.text_model.parameters(), 'lr': 1e-5},
    {'params': model.module.image_model.parameters(), 'lr': 5e-5},
    {'params': list(model.module.fc_image.parameters()) +
               list(model.module.fc_text.parameters()) +
               list(model.module.fusion.parameters()) +
               list(model.module.fc_final.parameters()), 'lr': 1e-4}
], weight_decay=1e-5)

scheduler = lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', factor=0.5, patience=0, min_lr=1e-6, verbose=True)
num_epochs = 20

def train_model(model, train_loader, val_loader, criterion, optimizer, scheduler, num_epochs):
    early_stopping = EarlyStopping(patience=5, verbose=True)
    
  # Training loop
    for epoch in range(num_epochs):
        model.train()
        running_loss = 0.0

        for input_ids, attention_mask, label, img in train_loader:
            input_ids = input_ids.to(device)
            attention_mask = attention_mask.to(device)
            label = label.to(device)
            img = img.to(device)
                
            optimizer.zero_grad()

          # Forward pass
            outputs = model(img, input_ids, attention_mask)
            loss = criterion(outputs, label)

          # Backward pass and optimization
            loss.backward()
            torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
            optimizer.step()

            running_loss += loss.item()* img.size(0)
            
       # Validating model and ensuring loss is decreasing     
        model.eval()
        val_loss = 0.0
        correct_preds = 0
        with torch.no_grad():
            for input_ids, attention_mask, label, img in val_loader:
                input_ids = input_ids.to(device)
                attention_mask = attention_mask.to(device)
                label = label.to(device)
                img = img.to(device)
    
                outputs = model(img, input_ids, attention_mask)
                loss = criterion(outputs, label)
                val_loss += loss.item() * img.size(0)

                _, preds = torch.max(outputs, 1)
                correct_preds += torch.sum(preds == label)

        val_loss = val_loss / len(val_loader.dataset)
        accuracy = correct_preds.double() / len(val_loader.dataset)
        scheduler.step(val_loss)
        print(f'Epoch {epoch+1}/{num_epochs}, Training Loss: {running_loss/len(train_loader.dataset):.4f}, Validation Loss: {val_loss:.4f}, Accuracy: {accuracy:.4f}')

        # Early stopping
        early_stopping(val_loss)
        if early_stopping.early_stop:
            print("Early stopping triggered. Stopping training.")
            break

    torch.save(model.state_dict(), '/kaggle/working/model2.pth')

In [20]:
from sklearn.metrics import precision_score, recall_score

def evaluate_model(model, test_loader, criterion):
    model.eval()
    val_losses = []
    correct_preds = 0

    all_preds = []
    all_labels = []

    with torch.no_grad():
        for input_ids, attention_mask, label, img in test_loader:
            input_ids = input_ids.to(device)
            attention_mask = attention_mask.to(device)
            label = label.to(device)
            img = img.to(device)

            outputs = model(
                  image = img,
                  text_input_ids = input_ids,
                  text_attention_mask = attention_mask
            )

            # Final Softmax layer returns class predictions per sample in batch
            # Highest probability value resembles class prediction and is assigned to preds variable
            _, preds = torch.max(outputs, dim=1)
            #print(outputs)

            # Loss is calculated by applying Cross Entropy Loss
            val_loss = criterion(outputs, label)

            # Counting correct model predictions and incrementing correct prediction count
            correct_preds += torch.sum(preds == label)
            print(preds, label)

            # Appending current loss per batch to list of losses per epoch
            val_losses.append(val_loss.item())
            
            all_preds.extend(preds.cpu().numpy())
            all_labels.extend(label.cpu().numpy())
            

    accuracy = float((correct_preds.double() / len(df_test)) * 100)
    precision = precision_score(all_labels, all_preds, average='weighted')
    recall = recall_score(all_labels, all_preds, average='weighted')

    print("\nAccuracy: ", accuracy)
    print("Precision: ", precision)
    print("Recall: ", recall)

In [21]:
train_model(model, train_loader,val_loader, criterion, optimizer, scheduler, num_epochs)
print("\n")
evaluate_model(model, test_loader, criterion)

Epoch 1/20, Training Loss: 0.1160, Validation Loss: 0.0951, Accuracy: 0.8409
Epoch 2/20, Training Loss: 0.0839, Validation Loss: 0.0968, Accuracy: 0.8478
EarlyStopping counter: 1 out of 5
Epoch 3/20, Training Loss: 0.0541, Validation Loss: 0.1117, Accuracy: 0.8513
EarlyStopping counter: 2 out of 5
Epoch 4/20, Training Loss: 0.0336, Validation Loss: 0.1642, Accuracy: 0.8517
EarlyStopping counter: 3 out of 5
Epoch 5/20, Training Loss: 0.0198, Validation Loss: 0.2515, Accuracy: 0.8484
EarlyStopping counter: 4 out of 5
Epoch 6/20, Training Loss: 0.0152, Validation Loss: 0.2819, Accuracy: 0.8484
EarlyStopping counter: 5 out of 5
Early stopping triggered. Stopping training.


tensor([0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 0, 0, 0, 1, 0, 1, 1, 1, 0,
        1, 1, 0, 0, 1, 0, 1, 1], device='cuda:0') tensor([0, 1, 1, 1, 0, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 0, 0, 1, 1, 1, 0,
        1, 1, 0, 1, 0, 0, 1, 0], device='cuda:0')
tensor([0, 0, 0, 1, 1, 1, 1, 0, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0,

In [22]:
torch.save(model, "/kaggle/working/model.pt")
torch.save(model.state_dict(), "/kaggle/working/state_dict.pth")    